# Uudiste meelsus (tonaalsus, polaarsus) 08. dets 20
Leksikonipõhine  ja sõnapõhine lähenemine

Inspiratsioon ja algallikad:
1. Väärinforiskid Eesti Meediaturul
GDI(The Global Disinformation Index - Globaalne Väärinformatsiooni Indeks) hindab uudistesaitide võimalikku kalduvust väärinfo vahendamisele.
"Artiklite tonaalsus on hea indikaator, mille abil ennustada uudisportaali teisi
väärinforiskidega seotud tugevuste ja nõrkuste seost teiste muutujatega.
Siin on oluline välja tuua tähelepanek, et artikli tonaalsuse ja väärinfo esinemise
tõenäosuse vahel on tugev seos."
https://disinformationindex.org/wp-content/uploads/2020/10/GDI-RiskRatingsReport_Estonian.pdf
2. IDENTIFYING POLARITY IN DIFFERENT TEXT TYPES
http://www.folklore.ee/folklore/vol64/polarity.pdf
3. Meelestatuse analüüs
http://samm.ut.ee/meelestatuse-anal%C3%BC%C3%BCs
4. Quantifying Mental Health Signals in Twitter
https://www.aclweb.org/anthology/W14-3207.pdf
5. Emotsioonidetektor
http://peeter.eki.ee:5000/valence
6.Emotsioonid – Kõnetehnoloogia olevik ja tulevik Hille Pajupuu
https://www.academia.edu/7169398/Emotsioonid_k%C3%B5netehnoloogia_olevik_ja_tulevik

Mida tehti?

1) Kasutada Eesti Keele Instituudi emotsioonileksikoni (estonian-emotion-lexicon.csv), mis sisaldab 39100 eestikeelset sõna koos skooriga. Skoor võib olla kas negatiivne (-1, -8) või positiivne (+1);

2) Kasutada EstNLTK teeki sõnaliikide tuvastamiseks

    a) esimesele isikule viitavate verbivormide leidmine ('gem','ks','ksime', 'ksin', 'me', 'n', 'neg gem', 'neg ks', 'neg me', 'neg nud', 'neg nuks', 'neg o', 'neg vat', 'nuks','nuksime', 'nuksin', 'nuvat', 'sime', 'sin', 'vat')
    
    b) esimesele isikule viitavate asesõnade leidmine ('mina', 'ma', 'meie', 'me')

Miks tehti? 

Algallikatele toetudes arvati, et negatiivsus ja esimese isiku kasutamine võivad olla uudise meelsuse näitajaks. (Eestikeelse emotsioonileksikoni kasutamise kohta on tehtud teadustöid, millele tugineti. Esimese isiku kasutamise kohta eestikeelses teaduskirjanduses viiteid ei leitud. Esimese isiku kasutamist näitajana peab seetõttu veel kaaluma.)

Kuidas?

Eesmärgiks leida uudisartiklile meelsuse (tonaalsuse, polaarsuse ) näitaja, mis arvestab artiklis kasutatud sõnade negatiivsust ja esimese isiku kasutust (verbid, asesõnad). 

Mis leiti?

Iga uudisartikli kohta leiti:

1) uudise pikkus sõnades

2) negatiivsete sõnade arv;

3) esimeses isikus kasutatud sõnade arv;

4) uudise skoor = negatiivsete sõnade arv + esimeses isikus kasutatud sõnade arv;

5) uudise kordaja = uudise skoor/uudise pikkus sõnades*;

6) positiivsete sõnade arv;

Kogu korpuse kohta leiti:
eelmistes punktides toodu, lisaks artiklites kasutatud negatiivsete ja positiivsete sõnade list.

*Positiivsete sõnade arv ei kajastu kordajas.

Väljastatakse skooride tabel, mille veergudeks on:

sõnade arv uudises

esimeses isikus sõnade arv

negatiivsete sõnade arv

uudise kordaja

positiivsete sõnade arv

väljaande nimi

uudise pealkiri

Probleemid:
1) uudiste tekstid korjatud BeautifulSoup abil. Kõiki tekste ei saa korrektselt kätte.

2) uudiste tekstide hulka on sattunud ka mitteoodatuid (näiteks videod) või vale rubriigiga (näiteks krimiuudised)

3) hetkel LAHENDAMATA probleem: 

        text = Text(uudis).tag_layer()
        uudise_pikkus_sõnades = len(text.words.text)
leidub uudiseid, mille pikkus sõnades on vale, praegu ei ole põhjust leidnud. Seetõttu läheb ka skoor valeks.

4) tänu eelmisele probleemile ei saa usaldada skooride tabelit

5) MÕELDA, kas uudise skoori arvutamisel veel mingi suurus juurde lisada

5) MÕELDA, mida korrektsete skooride tabeliga edasi teha

In [232]:
import csv
import pandas as pd
from estnltk import Text
from tqdm import tqdm

asesõnad = ['mina', 'ma', 'meie', 'me']
verbid = ['gem','ks','ksime', 'ksin', 'me', 'n', 'neg gem', 'neg ks', 'neg me', 'neg nud', 'neg nuks', 'neg o', 'neg vat', 'nuks'
         'nuksime', 'nuksin', 'nuvat', 'sime', 'sin', 'vat']
leksikon = {}
with open('estonian-emotion-lexicon.csv') as csv_file:
    reader = csv.reader(csv_file, delimiter=';')
    header = next(reader)
    for row in reader:
        leksikon[row[0]]= row[1]

In [208]:
def uudise_skoor(uudised): # sisend DataFrame ja väljaande nimi
    esimese_isiku_kasutus = 0
    negatiivsus = 0
    positiivsus = 0
    negatiivsed_sonad_list = []
    positiivsed_sonad_list = []
    uudiste_pikkus_sõnades = 0
    uudisdict= {}
    pikkus =[]
    esimene_isik = []
    neg = []
    kordaja = []
    pos =[]
    print("Analüüsitakse", len(uudised.text),"uudist.")

    for i, uudis in tqdm(enumerate(uudised.text)):
    
        text = Text(uudis).tag_layer()
        uudise_pikkus_sõnades = len(text.words.text)
        if uudise_pikkus_sõnades !=0:
            uudiste_pikkus_sõnades += uudise_pikkus_sõnades

            a_sõnade_arv = 0
            v_sõnade_arv = 0
            esimene_isik_arv = 0
            negatiivsete_arv = 0
            positiivsete_arv = 0

            morf = text.morph_analysis
            for sõna in morf:

                if sõna.text in leksikon:

                    if int(leksikon[sõna.text]) < 0:
                        negatiivsed_sonad_list.append(sõna.text)
                        negatiivsete_arv -= int(leksikon[sõna.text])

                    if int(leksikon[sõna.text]) > 0:
                        positiivsed_sonad_list.append(sõna.text)
                        positiivsete_arv += int(leksikon[sõna.text])

                if sõna.partofspeech[0]  == 'V': #verb
                    if sõna.form[0] in verbid:
                        v_sõnade_arv += 1
                if sõna.text in asesõnad:
                    a_sõnade_arv += 1
            esimene_isik_arv = a_sõnade_arv + v_sõnade_arv
            esimese_isiku_kasutus += esimene_isik_arv
            negatiivsus += negatiivsete_arv
            uudise_skoor = esimene_isik_arv + negatiivsete_arv
            uudise_kordaja = uudise_skoor/uudise_pikkus_sõnades
            positiivsus += positiivsete_arv
            
            pikkus.append(uudise_pikkus_sõnades)
            esimene_isik.append(esimene_isik_arv)
            neg.append(negatiivsete_arv)
            kordaja.append(round(uudise_kordaja*100, 2))
            pos.append(positiivsete_arv)

    uudisdict = {'sõnu uudises':pikkus,'esimene isik': esimene_isik, 'negatiivsus': neg, 'kordaja':kordaja, 'positiivsus':pos}

    statistika = pd.DataFrame(uudisdict, columns = ['sõnu uudises', 'esimene isik', 'negatiivsus', 'kordaja', 'positiivsus'])
    statistika['väljaanne'] = uudised['subject']  
    statistika['pealkiri'] = uudised['title']
    
    print('Korpuses 1. isiku kasutamine', esimese_isiku_kasutus)
    print('Korpuses negatiivsus', negatiivsus)
    skoor = esimese_isiku_kasutus + negatiivsus
    print("Korpuse uudiste skoor: ", skoor)
    print("Korpuse uudiste pikkus sõnades: ", uudiste_pikkus_sõnades)
    print("Korpuse kordaja: ", round(skoor/uudiste_pikkus_sõnades*100, 2))
    print("Korpuse positiivsus", positiivsus)
    print("Korpuses negatiivseid sõnu: ", len(negatiivsed_sonad_list), negatiivsed_sonad_list)
    print("Korpuses positiivseid sõnu: ", len(positiivsed_sonad_list), positiivsed_sonad_list)
    return statistika

In [233]:
data_delfi = pd.read_csv("data_delfi_arhiiv_03122020.csv").dropna()
data_telegram_rubriigid = pd.read_csv("data_telegram_rubriigid_arhiiv.csv").dropna()
data_uueduudised_rubriigid = pd.read_csv("data_uueduudised_rubriigid_arhiiv.csv").dropna()
# Ebavajaliku info eemaldamine
data_delfi.drop(["date"],axis=1,inplace=True)
data_telegram_rubriigid.drop(["date"],axis=1,inplace=True)
data_uueduudised_rubriigid.drop(["date"],axis=1,inplace=True)

In [235]:
data_delfi.shape

(6152, 3)

In [236]:
delfi_skoorid = uudise_skoor(data_delfi)

2it [00:00, 13.10it/s]

Analüüsitakse 6152 uudist.


6152it [13:17,  7.72it/s]


Korpuses 1. isiku kasutamine 24193
Korpuses negatiivsus 38422
Korpuse uudiste skoor:  62615
Korpuse uudiste pikkus sõnades:  1571241
Korpuse kordaja:  3.99
Korpuse positiivsus 37478
Korpuses negatiivseid sõnu:  38373 ['loobuda', 'kahjuks', 'probleeme', 'negatiivset', 'hullem', 'võitlust', 'õnnetute', 'kannatab', 'kaotanud', 'väsimus', 'viirusega', 'nohu', 'raske', 'jõuetus', 'kummalised', 'väsinud', 'hullem', 'väsimus', 'haigete', 'haigusi', 'haigete', 'poleks', 'karmimaid', 'pole', 'pole', 'süüdistatakse', 'vanglas', 'vahistatud', 'süüdistatakse', 'vanglakaristus', 'lahutada', 'keelatud', 'häbenema', 'igav', 'kriisi', 'sõjast', 'ohtudele', 'sõjast', 'puuduta', 'viiruse', 'mureks', 'kontrolli', 'vastases', 'võitluses', 'kurjaks', 'salajastes', 'kulutatud', 'pole', 'suits', 'karjus', 'suitsu', 'põgeneda', 'kannatanu', 'petsid', 'haige', 'surve', 'ähvardab', 'mure', 'surve', 'kriitikat', 'ohtu', 'oht', 'pole', 'halb', 'pole', 'kahelda', 'oht', 'polnud', 'kontrolli', 'kontrolli', 'polnud'

In [237]:
delfi_skoorid

sõnu uudises  esimene isik  negatiivsus  kordaja  positiivsus  \
0              181             7            3     5.52            2   
1              134             5            0     3.73            2   
2              306             2           15     5.56            8   
3              186             7            7     7.53            6   
4              146             0            5     3.42            0   
...            ...           ...          ...      ...          ...   
6147           303             1           12     4.29            7   
6148           203             0            6     2.96            5   
6149           156             1            5     3.85            6   
6150           367             0            0     0.00            3   
6151           269             0           15     5.58            1   

            väljaanne  \
0               Delfi   
1               Delfi   
2     Eesti Päevaleht   
3               Delfi   
4               Delfi   
...               ...   
6147            Delfi   
6148            Delfi   
6149            Delfi   
6150            Delfi   
6151            Delfi   

                                                                                                                                                                 pealkiri  
0                                                                                                         Sotsiaalminister Kiik: uusi piiranguid ei saa kahjuks välistada  
1                                      FOTOD | Sillamäe elanikud ootavad vene vaktsiini tulekut, aga COVID-19 profülaktikaks söövad küüslauku ja pesevad käsi pesuseebiga  
2     Paljud koroonahaiged ei taastugi. Kuus eestlast räägivad oma loo kuudepikkusest võitlusest: „See imeb su kuivaks, tühjaks. Pead uuesti alustama.” - Eesti Päevaleht  
3                                                                                                           Maris Jesse: enne märtsi tavainimesed koroonavaktsiini ei saa  
4                                                                                          Vene riigi reetmises kahtlustatav Sergei Lõhmus astub homme Pihkvas kohtu ette  
...                                                                                                                                                                   ...  
6147                                                            Tööliste pendelrände lubamise tagajärg: Soomest on Eestisse viimasel ajal toodud kokku 10 koroonajuhtumit  
6148                                                                                    ANNA TEADA | Oled üks koroonaohvritest? Kirjuta oma kogemusest töökoha kaotamisel  
6149                           Kõik polegi seaduse ees võrdsed? Raivo Aeg: taunimisväärne, et Mary Kross pääses puhtalt, aga samamoodi valetanud tartlanna mõisteti süüdi  
6150                                                                               Aftonbladet: Rootsi riigiepidemioloog Anders Tegnell on saanud mitmeid tapmisähvardusi  
6151                                                      Viroloog Andres Merits: uut viirusepuhangut tuleb pidada tõenäoliseks, selle ulatus sõltub inimeste käitumisest  

[6152 rows x 7 columns]

In [241]:
data_telegram_rubriigid.shape

(6264, 4)

In [242]:
telegram_skoorid = uudise_skoor(data_telegram_rubriigid)

0it [00:00, ?it/s]

Analüüsitakse 6264 uudist.


6264it [29:59,  3.48it/s]


Korpuses 1. isiku kasutamine 67413
Korpuses negatiivsus 82689
Korpuse uudiste skoor:  150102
Korpuse uudiste pikkus sõnades:  3539259
Korpuse kordaja:  4.24
Korpuse positiivsus 91147
Korpuses negatiivseid sõnu:  82367 ['ohtlik', 'viirus', 'pole', 'viirus', 'ohtlik', 'viirus', 'viirusega', 'haige', 'vähem', 'viirusesse', 'surnud', 'vastuolus', 'viirus', 'kohustuslikuks', 'viiruse', 'kriitiline', 'kukkumas', 'mures', 'mure', 'kardab', 'surema', 'puudub', 'puudub', 'vale', 'kahelda', 'kahtluste', 'hirmude', 'hirm', 'hirm', 'kaotanud', 'hirm', 'lööd', 'kinnises', 'vastased', 'kurta', 'kaotada', 'pole', 'kohustuseks', 'karistust', 'ohtlik', 'ohtlik', 'kohustus', 'kartma', 'ohtlikud', 'kannatavad', 'ohtlikuks', 'pole', 'nõrgemale', 'nõrgem', 'nõrgem', 'kaotanud', 'raskematel', 'kodutuid', 'kodutuid', 'haigeid', 'lastekodudes', 'polnud', 'pole', 'stress', 'kinnises', 'kriis', 'kaotavad', 'keeld', 'keeld', 'ohtlik', 'pole', 'pole', 'töötud', 'töötud', 'ohtlik', 'pinge', 'kukub', 'pinge', 'ping

In [243]:
telegram_skoorid

sõnu uudises  esimene isik  negatiivsus  kordaja  positiivsus väljaanne  \
0              399             9           17     6.52            8  Telegram   
1             1232            89           43    10.71           47  Telegram   
2              655            39           31    10.69           15  Telegram   
3              943            30           27     6.04           32  Telegram   
4              805            19           25     5.47           19  Telegram   
...            ...           ...          ...      ...          ...       ...   
6259           670             1           13     2.09            8  Telegram   
6260           202             3            4     3.47            6  Telegram   
6261           156             0            9     5.77            3  Telegram   
6262           314             0            7     2.23            4  Telegram   
6263           281             5            4     3.20            4  Telegram   

                                                                                                                     pealkiri  
0                                                Mõttekoht: Kas maskide kandmine hoopis soodustab viiruse levikut? | Telegram  
1     Carmen Pritsoni "Vabadus Vabalt Hingata" kõne: Küsimus ei ole juba ammu ainult maskides. Küsimus on fookuses | Telegram  
2                                                       Repliik: Sõbrad kaotavad päevapealt töö. Aitäh, et hoolid! | Telegram  
3                                                    Ülemaailmsed meeleavaldused koguvad tuure – rahval on küllalt | Telegram  
4                            Allar Jõksi sõnul pole maskinõue seaduslik: valitsus on oma pädevust selgelt ületanud | Telegram  
...                                                                                                                       ...  
6259                                                   Hiina õhusaaste tulemus: poes müüakse purkides värsket õhku | Telegram  
6260                                                    Washington kiitis heaks keemiarünnaku lavastamise Süürias? | Telegram  
6261                    Ülekäte läinud politseiriik: abielupaari ähvardab hirvebeebi päästmise eest vanglakaristus | Telegram  
6262                                                            Soome rahvas tahab EL-ist ja eurotsoonist lahkuda? | Telegram  
6263                                           Pressiskandaal: Postimees üritab takistada Telegrami ajakirja müüki | Telegram  

[6264 rows x 7 columns]

In [244]:
data_uueduudised_rubriigid.shape

(6999, 4)

In [245]:
uueduudised_skoorid = uudise_skoor(data_uueduudised_rubriigid)

0it [00:00, ?it/s]

Analüüsitakse 6999 uudist.


6999it [23:58,  4.86it/s]


Korpuses 1. isiku kasutamine 55512
Korpuses negatiivsus 76663
Korpuse uudiste skoor:  132175
Korpuse uudiste pikkus sõnades:  2936451
Korpuse kordaja:  4.5
Korpuse positiivsus 80910
Korpuses negatiivseid sõnu:  76243 ['keelamist', 'keelamine', 'keelamiseks', 'rikkuda', 'võitlusega', 'keeld', 'kaotada', 'rikkuda', 'keelamise', 'puuduvad', 'vaidlustes', 'pole', 'muretsevad', 'pole', 'probleemi', 'pole', 'häda', 'valusaid', 'pole', 'keelamist', 'hädade', 'pole', 'vaese', 'probleem', 'karmidel', 'raskeks', 'probleemiks', 'valusale', 'pole', 'pole', 'tapjad', 'pole', 'karmidest', 'kannatustest', 'hoolimatus', 'süüdistavad', 'võitlustesse', 'puudumisest', 'pole', 'haigustest', 'õnnetustest', 'peksab', 'poleks', 'raskeks', 'muretseda', 'pole', 'raske', 'raske', 'vägivald', 'petta', 'süüdistama', 'eksinud', 'kukkunud', 'valesti', 'muredes', 'võitlustes', 'salajase', 'pimedal', 'kahju', 'pimedal', 'surnute', 'kahju', 'vale', 'häbeneb', 'häbeneb', 'rumalad', 'kannatusi', 'hilinemisega', 'problee

In [246]:
uueduudised_skoorid

sõnu uudises  esimene isik  negatiivsus  kordaja  positiivsus  \
0             1708            34           45     4.63           53   
1              262             5            5     3.82           12   
2              934            24           17     4.39           34   
3              204             4            7     5.39            6   
4              217             3            2     2.30            2   
...            ...           ...          ...      ...          ...   
6994           222             5            9     6.31            1   
6995           211             1           16     8.06            2   
6996           325             9            6     4.62            4   
6997           420             3           18     5.00            4   
6998           233             0            9     3.86            3   

         väljaanne  \
0     Uued Uudised   
1     Uued Uudised   
2     Uued Uudised   
3     Uued Uudised   
4     Uued Uudised   
...            ...   
6994  Uued Uudised   
6995  Uued Uudised   
6996  Uued Uudised   
6997  Uued Uudised   
6998  Uued Uudised   

                                                                                                                                                     pealkiri  
0                                                                       Teravaks muudetud aborditeemalon vähe ühist probleemi inimliku küljega - Uued Uudised  
1                                       Andres Raid "eestikeelsest haridusest": haridus on osa isiksusest, teatud keeles toimub vaid õpetamine - Uued Uudised  
2                                                       Helle-Moonika Helme jõulukolumn: "Anna neile andeks, sest nad ei tea, mida nad teevad" - Uued Uudised  
3                                                          Peep Leppik: küsimus pole niivõrd keeles kui õpetamise tasemes Eesti koolides üldse - Uued Uudised  
4     Helle-Moonika Helme: "Kõige küünilisem on see, et eesti lapsed peavad hakkama tegema seda tööd, mida Reformierakond 17 aastat ei teinud" - Uued Uudised  
...                                                                                                                                                       ...  
6994                                               Rootsi valimised ja "demokraatia": uusparempoolsete juht Jimmie Åkesson sai tapmisähvarduse - Uued Uudised  
6995                                                                                         Trump: Woodwardi raamat kubiseb valest ja laimust - Uued Uudised  
6996                                                             Pagulaskeskused "lekivad", kadunud migrandid võivad levitada ohtlikke nakkusi - Uued Uudised  
6997                                                                               Kas New York Times korraldas infooperatsiooni Trumpi vastu? - Uued Uudised  
6998                                         Breitbart: kahed matused, mida Ameerika vulgaarne meedia ja poliitiline eliit tsirkuseks pöörasid - Uued Uudised  

[6999 rows x 7 columns]

In [255]:
skoorid = pd.concat([delfi_skoorid, telegram_skoorid, uueduudised_skoorid])

In [256]:

skoorid.sort_values(by=['kordaja'], inplace=True, ascending=False)


In [261]:
skoorid.shape

(19415, 7)

In [262]:
#sorteeritud kahanevalt kordaja järgi
skoorid

sõnu uudises  esimene isik  negatiivsus  kordaja  positiivsus  \
1121             2             1            0    50.00            0   
1898            14             2            3    35.71            1   
260              3             1            0    33.33            0   
3438            11             1            2    27.27            0   
766            114             1           27    24.56            3   
...            ...           ...          ...      ...          ...   
1305            74             0            0     0.00            1   
417             37             0            0     0.00            0   
418             50             0            0     0.00            0   
419              6             0            0     0.00            0   
5943           195             0            0     0.00            2   

         väljaanne  \
1121      Telegram   
1898         Delfi   
260          Delfi   
3438         Delfi   
766   Uued Uudised   
...            ...   
1305         Delfi   
417       Telegram   
418       Telegram   
419       Telegram   
5943      Telegram   

                                                                                                   pealkiri  
1121                               Altruistlik idee: "Mässav" pank vabastab londonlasi võlgadest | Telegram  
1898                   Soome uurimisametkonna juht Rootsi lehe artiklist Estonia kohta: ei pea paika, jama!  
260                                                          Pärnus Kõpu külas hukkus liiklusõnnetuses mees  
3438                      SELGITAV VIDEO | Need on 4 asja, mille tõttu võiks Lukašenka lõpuks võimu kaotada  
766                       "Valitsusele molli!" Delfi on hakanud kasutama rullnoka kõnepruuki - Uued Uudised  
...                                                                                                     ...  
1305  Tanel Kiik: koroonaviiruse leviku hoogustumine teeb muret, aga uusi piiranguid valitsuse laual ei ole  
417                                               Ajatu: Kas vähki on täiesti valesti mõistetud? | Telegram  
418                                         Telegrami järjejutt: Ennustused, mis läksid täide II | Telegram  
419                                          Telegrami järjejutt: Ennustused, mis läksid täide I | Telegram  
5943                                                 Medvedev: Küprosel röövitakse kokkuröövitut | Telegram  

[19415 rows x 7 columns]